# Basic example

Sinergym uses the standard OpenAI gym API. Lets see how to create a basic loop.

First we need to include sinergym and create an environment, in our case using 'Eplus-demo-v1'

In [2]:
import gymnasium as gym
import numpy as np

import sinergym

In [ ]:
env = gym.make('Eplus-demo-v1')

At first glance may appear that sinergym is only imported but never used, but by importing Sinergym all its [Environments](https://ugr-sail.github.io/sinergym/compilation/html/pages/environments.html)
are defined to be used, in this case 'Eplus-demo-v1' with all the information contained in the idf file and the config file.

After this simple definition we are ready to loop the episodes, for this simple example we are going to consider only 1 episode. In summary the code we need is something like this:

In [4]:
for i in range(1):
    obs, info = env.reset()
    rewards = []
    observations = []
    terminated = False
    current_month = 0
    while not terminated:
        a = env.action_space.sample()
        obs, reward, terminated, truncated, info = env.step(a)
#         print('Obs: ', obs)
        rewards.append(reward)
        observations.append(obs)
        if info['month'] != current_month:  # display results every month
            current_month = info['month']
            print('Reward: ', sum(rewards), info)

[2023-05-17 05:43:41,335] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Creating new EnergyPlus simulation episode...
[2023-05-17 05:43:41,519] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:EnergyPlus working directory is in /root/my-project/examples/Eplus-env-demo-v1-res8/Eplus-env-sub_run1


/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


Reward:  -0.18054534463652905 {'timestep': 1, 'time_elapsed': 900, 'year': 1991, 'month': 1, 'day': 1, 'hour': 0, 'action': [21, 21], 'reward': -0.18054534463652905, 'reward_energy': -1.8054534463652903, 'reward_comfort': -0.0, 'total_energy': 18054.5344636529, 'abs_comfort': 0.0, 'temperatures': [20.99998833869494, 20.81866975215882, 20.9999880037787, 20.71504075275832, 20.99998305378782]}
Reward:  -5763.117736881167 {'timestep': 2976, 'time_elapsed': 2678400, 'year': 1991, 'month': 2, 'day': 1, 'hour': 0, 'action': [22, 23], 'reward': -0.2266049065564041, 'reward_energy': -2.266049065564041, 'reward_comfort': -0.0, 'total_energy': 22660.49065564041, 'abs_comfort': 0.0, 'temperatures': [21.64848453584105, 20.27223518090898, 21.59761757334702, 20.19741394829678, 20.66473502531415]}
Reward:  -12028.195440598773 {'timestep': 5664, 'time_elapsed': 5097600, 'year': 1991, 'month': 3, 'day': 1, 'hour': 0, 'action': [20, 25], 'reward': -0.32230673238890206, 'reward_energy': -0.974010773646954

Now we can see the final rewards:

In [5]:
print(
    'Mean reward: ',
    np.mean(rewards),
    'Cumulative reward: ',
    sum(rewards))

Mean reward:  -3.389259588758715 Cumulative reward:  -118759.65599010859


The [list of environments](https://github.com/ugr-sail/sinergym/blob/main/sinergym/__init__.py) that we have registered in Sinergym is extensive and we use buildings changing particularities. For example, continuous action space or discrete, noise over weather, runperiod, timesteps, reward function, etc. We will see it in the following notebooks.****

In [6]:
env.variables['observation']

['year',
 'month',
 'day',
 'hour',
 'Site Outdoor Air Drybulb Temperature(Environment)',
 'Site Outdoor Air Relative Humidity(Environment)',
 'Site Wind Speed(Environment)',
 'Site Wind Direction(Environment)',
 'Site Diffuse Solar Radiation Rate per Area(Environment)',
 'Site Direct Solar Radiation Rate per Area(Environment)',
 'Zone Thermostat Heating Setpoint Temperature(SPACE1-1)',
 'Zone Thermostat Cooling Setpoint Temperature(SPACE1-1)',
 'Zone Air Temperature(SPACE1-1)',
 'Zone Air Temperature(SPACE2-1)',
 'Zone Air Temperature(SPACE3-1)',
 'Zone Air Temperature(SPACE4-1)',
 'Zone Air Temperature(SPACE5-1)',
 'Zone Thermal Comfort Mean Radiant Temperature(SPACE1-1 PEOPLE 1)',
 'Zone Air Relative Humidity(SPACE1-1)',
 'Zone Thermal Comfort Clothing Value(SPACE1-1 PEOPLE 1)',
 'Zone Thermal Comfort Fanger Model PPD(SPACE1-1 PEOPLE 1)',
 'Zone People Occupant Count(SPACE1-1)',
 'People Air Temperature(SPACE1-1 PEOPLE 1)',
 'Facility Total HVAC Electricity Demand Rate(Whole Buildin

In [7]:
observations[0]

array([1.9910000e+03, 1.0000000e+00, 1.0000000e+00, 0.0000000e+00,
       1.8000000e+00, 9.5250000e+01, 4.0999999e+00, 2.6500000e+02,
       0.0000000e+00, 0.0000000e+00, 2.1000000e+01, 2.1000000e+01,
       2.0999989e+01, 2.0818670e+01, 2.0999989e+01, 2.0715040e+01,
       2.0999983e+01, 1.9362980e+01, 3.9579979e+01, 7.5000000e-01,
       2.9739861e+01, 0.0000000e+00, 2.0999989e+01, 1.8054535e+04],
      dtype=float32)

And as always don't forget to close the environment:

In [ ]:
env.close()

# Custom Stuff

In [1]:
import gymnasium as gym
import numpy as np

import sinergym
from sinergym.utils.rewards import LinearReward, BaseReward
from sinergym.utils import env_checker
from datetime import datetime
from math import exp
from typing import Any, Dict, List, Tuple, Union

In [2]:
# For checking custom env
# env_checker.check_env(env)

In [3]:
class CustomReward(BaseReward):
    def __init__(
        self,
        temperature_variable: Union[str, list],
        occupancy_variable: Union[str, list],
        energy_variable: str,
        range_comfort_winter: Tuple[int, int],
        range_comfort_summer: Tuple[int, int],
        summer_start: Tuple[int, int] = (6, 1),
        summer_final: Tuple[int, int] = (9, 30),
        energy_weight: float = 0.5,
        lambda_energy: float = 1e-4,
        lambda_temperature: float = 1.0
    ):
        """
        Linear reward function.

        It considers the energy consumption and the absolute difference to temperature comfort.

        .. math::
            R = - W * lambda_E * power - (1 - W) * lambda_T * (max(T - T_{low}, 0) + max(T_{up} - T, 0))

        Args:
            temperature_variable (Union[str, list]): Name(s) of the temperature variable(s).
            occupancy_variable (Union[str, list]): Name(s) of the occupancy variable(s).
            energy_variable (str): Name of the energy/power variable.
            range_comfort_winter (Tuple[int,int]): Temperature comfort range for cold season. Depends on environment you are using.
            range_comfort_summer (Tuple[int,int]): Temperature comfort range for hot season. Depends on environment you are using.
            summer_start (Tuple[int,int]): Summer session tuple with month and day start. Defaults to (6,1).
            summer_final (Tuple[int,int]): Summer session tuple with month and day end. defaults to (9,30).
            energy_weight (float, optional): Weight given to the energy term. Defaults to 0.5.
            lambda_energy (float, optional): Constant for removing dimensions from power(1/W). Defaults to 1e-4.
            lambda_temperature (float, optional): Constant for removing dimensions from temperature(1/C). Defaults to 1.0.
        """

        super(CustomReward, self).__init__()
        
        # Check that occupancy_variable is of same type [str, list] as temperature_variable. 
        # If both are lists, check that they have same length.
        if (type(temperature_variable) == type(occupancy_variable)):
            if (type(temperature_variable) == list and len(temperature_variable) != len(occupancy_variable)):
                raise Exception("temperature_variable should have the same length as occupancy_variable")
        else: 
            raise Exception("temperature_variable must be of same type as occupancy_variable")

        # Name of the variables
        self.temp_name = temperature_variable
        self.occ_name = occupancy_variable
        self.energy_name = energy_variable

        # Reward parameters
        self.range_comfort_winter = range_comfort_winter
        self.range_comfort_summer = range_comfort_summer
        self.W_energy = energy_weight
        self.lambda_energy = lambda_energy
        self.lambda_temp = lambda_temperature

        # Summer period
        self.summer_start = summer_start  # (month,day)
        self.summer_final = summer_final  # (month,day)

    def __call__(self, obs_dict: Dict[str, Any]
                 ) -> Tuple[float, Dict[str, Any]]:
        """Calculate the reward function.

        Args:
            obs_dict (Dict[str, Any]): Dict with observation variable name (key) and observation variable value (value)

        Returns:
            Tuple[float, Dict[str, Any]]: Reward value and dictionary with their individual components.
        """

        # Energy term
        reward_energy = - self.lambda_energy * obs_dict[self.energy_name]

        # Comfort
        comfort, temps = self._get_comfort(obs_dict)
        
        # Comfort is an array of comforts
        abs_comfort = sum(comfort)
        
        # TODO: Continue from here!
        occs = [v for k, v in obs_dict.items() if k in self.occ_name]
        print("comfort: ", comfort)
        print("occs: ", occs) # occs is a list of floats of the actual number of people, eg: [0.0, 2.0, 11.0, 22.0]
        reward = 0
        reward_comfort = 0
        zone_reward_energy = reward_energy / len(occs)
        for zone_comf, zone_occ in zip(comfort, occs):
            reward_comfort = - self.lambda_temp * zone_comf
            weight = self.W_energy if zone_occ > 0.0 else 0.75 # Replace hardcoded value with new variable W_energy_unoccupied
            # Weighted sum of both terms
            reward += weight * zone_reward_energy + \
                (1.0 - weight) * reward_comfort
            
#         reward_comfort = - self.lambda_temp * abs_comfort
#         # Weighted sum of both terms
#         reward = self.W_energy * reward_energy + \
#             (1.0 - self.W_energy) * reward_comfort

        reward_terms = {
            'reward_energy': reward_energy,
            'reward_comfort': reward_comfort, # Note: this is per zone reward comfort
            'total_energy': obs_dict[self.energy_name],
            'abs_comfort': abs_comfort,
            'temperatures': temps
        }

        return reward, reward_terms

    def _get_comfort(self,
                     obs_dict: Dict[str,
                                    Any]) -> Tuple[Union[float, List[float]],
                                                   List[float]]:
        """Calculate the comfort term of the reward.

        Returns:
            Tuple[float, List[float]]: comfort penalty and List with temperatures used.
        """

        month = obs_dict['month']
        day = obs_dict['day']
        year = obs_dict['year']
        current_dt = datetime(int(year), int(month), int(day))

        # Periods
        summer_start_date = datetime(
            int(year),
            self.summer_start[0],
            self.summer_start[1])
        summer_final_date = datetime(
            int(year),
            self.summer_final[0],
            self.summer_final[1])

        if current_dt >= summer_start_date and current_dt <= summer_final_date:
            temp_range = self.range_comfort_summer
        else:
            temp_range = self.range_comfort_winter

        temps = [v for k, v in obs_dict.items() if k in self.temp_name]
#         occs = [v for k, v in obs_dict.items() if k in self.occ_name]
        comfort = []
        for T in temps:
            if T < temp_range[0] or T > temp_range[1]:
                comfort.append(min(abs(temp_range[0] - T), abs(T - temp_range[1])))
            else:
                comfort.append(0.0)

        return comfort, temps

In [4]:
OBSERVATION_VARIABLES=[
        'Site Outdoor Air Drybulb Temperature(Environment)',
        'Site Outdoor Air Relative Humidity(Environment)',
        'Site Wind Speed(Environment)',
        'Site Wind Direction(Environment)',
        'Site Diffuse Solar Radiation Rate per Area(Environment)',
        'Site Direct Solar Radiation Rate per Area(Environment)',
        'Zone Thermostat Heating Setpoint Temperature(SPACE1-1)',
        'Zone Thermostat Cooling Setpoint Temperature(SPACE1-1)',
        'Zone Air Temperature(SPACE1-1)',
        'Zone Air Temperature(SPACE2-1)',
        'Zone Air Temperature(SPACE3-1)',
        'Zone Air Temperature(SPACE4-1)',
        'Zone Air Temperature(SPACE5-1)',
        'Zone Thermal Comfort Mean Radiant Temperature(SPACE1-1 PEOPLE 1)',
        'Zone Air Relative Humidity(SPACE1-1)',
        'Zone Thermal Comfort Clothing Value(SPACE1-1 PEOPLE 1)',
        'Zone Thermal Comfort Fanger Model PPD(SPACE1-1 PEOPLE 1)',
        'Zone People Occupant Count(SPACE1-1)',
        'Zone People Occupant Count(SPACE2-1)',
        'Zone People Occupant Count(SPACE3-1)',
        'Zone People Occupant Count(SPACE4-1)',
        'Zone People Occupant Count(SPACE5-1)',
        'People Air Temperature(SPACE1-1 PEOPLE 1)',
        'Facility Total HVAC Electricity Demand Rate(Whole Building)'
    ]

env = gym.make(
    'Eplus-demo-v1', 
    observation_space= gym.spaces.Box(
        low=-5e6,
        high=5e6,
        shape=(len(OBSERVATION_VARIABLES) + 4,),
        dtype=np.float32
    ),
    observation_variables=OBSERVATION_VARIABLES,
    reward=CustomReward, 
    reward_kwargs={
        'temperature_variable': [
            'Zone Air Temperature(SPACE1-1)',
            'Zone Air Temperature(SPACE2-1)',
            'Zone Air Temperature(SPACE3-1)',
            'Zone Air Temperature(SPACE4-1)',
            'Zone Air Temperature(SPACE5-1)',
        ],
        'occupancy_variable': [
            'Zone People Occupant Count(SPACE1-1)',
            'Zone People Occupant Count(SPACE2-1)',
            'Zone People Occupant Count(SPACE3-1)',
            'Zone People Occupant Count(SPACE4-1)',
            'Zone People Occupant Count(SPACE5-1)',
        ],
        'energy_variable': 'Facility Total HVAC Electricity Demand Rate(Whole Building)',
        'range_comfort_winter': (20.0, 23.5),
        'range_comfort_summer': (23.0, 26.0),
        'energy_weight': 0.1
    }
)

[2023-05-17 09:21:29,950] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Updating idf ExternalInterface object if it is not present...
[2023-05-17 09:21:29,951] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Updating idf Site:Location and SizingPeriod:DesignDay(s) to weather and ddy file...
[2023-05-17 09:21:29,953] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Updating idf OutPut:Variable and variables XML tree model for BVCTB connection.
[2023-05-17 09:21:29,956] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Setting up extra configuration in building model if exists...
[2023-05-17 09:21:29,957] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Setting up action definition in building model if exists...


In [5]:
for i in range(1):
    obs, info = env.reset()
    rewards = []
    observations = []
    terminated = False
    current_month = 0
    while not terminated:
        a = env.action_space.sample()
        obs, reward, terminated, truncated, info = env.step(a)
#         print('Obs: ', obs)
        rewards.append(reward)
        observations.append(obs)
        if info['month'] != current_month:  # display results every month
            current_month = info['month']
            print('Reward: ', sum(rewards), info)

[2023-05-17 09:21:29,969] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:Creating new EnergyPlus simulation episode...
[2023-05-17 09:21:30,156] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:EnergyPlus working directory is in /root/my-project/examples/Eplus-env-demo-v1-res20/Eplus-env-sub_run1


/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


comfort:  [0.7607145700276305, 1.058953235921809, 0.7400394909393597, 1.12013148608321, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
Reward:  -1.2034724995769583 {'timestep': 1, 'time_elapsed': 900, 'year': 1991, 'month': 1, 'day': 1, 'hour': 0, 'action': [17, 28], 'reward': -1.2034724995769583, 'reward_energy': -0.3780170717786078, 'reward_comfort': -0.0, 'total_energy': 3780.170717786078, 'abs_comfort': 3.679838782972009, 'temperatures': [19.23928542997237, 18.94104676407819, 19.25996050906064, 18.87986851391679, 20.09605568964284]}
comfort:  [1.4387620552447302, 1.5699237243729414, 1.4135966735248608, 1.6054689929935009, 0.4008728690642194]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.0554840315018694, 1.0027823988348388, 1.0362278770785096, 1.0149677850573404, 0.48535454129459055]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.5383917342266002, 1.437103

comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.006333885388130511, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.10842619851987934, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.16713437426928834, 0.1145233837256292, 0.3392560580801991, 0.10911591925232855, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.3770964590277188, 0.27660545889169086, 0.4999112511261501, 0.2759425026540612, 0.0]
occs:  [11.0, 5.

comfort:  [0.0, 0.040938739931910106, 0.0, 0.10053268759513045, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.3100968725299715, 1.7643739900998412, 1.292895370284139, 1.7944004019783684, 0.4966988485888706]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.09820036145390176, 0.38126380680173, 0.09612052247220859, 0.42978391750052936, 0.04018319606944942]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.9486573156471785, 1.9682831549746709, 1.9193781428960683, 1.9879751750636316, 0.829708017973541]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.07399376413503944, 0.5551503255510291, 0.09314816217570865, 0.5945576368065204, 0.25499221391327964]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.19367067340171928, 0.0, 0.25051078777859104, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0913749662531913, 0.0, 0.1548719240609806, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.06702428387367121, 0.0

...

comfort:  [1.7044875823432797, 1.7292141411345305, 1.6884325494261283, 1.7371035899378988, 0.9388831049078199]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [2.096482802439951, 1.9965633387496204, 2.07644297377864, 1.9985994100413613, 1.0393042937708685]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.0830301892137193, 1.1474108915646006, 1.0808503154422908, 1.1545912195363996, 1.0017957594015492]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.018986667475100916, 0.0, 0.0672242628874109, 0.2193104987076886]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.629882502340589, 1.2662945644120818, 0.6312710990473285, 1.3056106656126296, 0.22705000004252085]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]

comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [5.5, 2.5, 5.5, 2.5, 10.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [5.5, 2.5, 5.5, 2.5, 10.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [5.5, 2.5, 5.5, 2.5, 10.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [5.5, 2.5, 5.5, 2.5, 10.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [1.1, 0.5, 1.1, 0.5, 2.0]
comfort:  [0.21787294172822058, 0.020831571054060305, 0.1647363491691607, 0.020844680725598863, 0.0]
occs:  [1.1, 0.5, 1.1, 0.5, 2.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [1.1, 0.5, 1.1, 0.5, 2.0]
comfort:  [0.23132037823575047, 0.09842525238504152, 0.1946097125414994, 0.09843213636390047, 0.0]
occs:  [1.1, 0.5, 1.1, 0.5, 2.0]
comfort:  [1.0445481891781405, 1.1490473459368893, 1.0070873305538903, 1.1695667547457695, 0.0]
occs

comfort:  [0.6537355848507893, 0.6584458163166396, 0.6410815211408014, 0.6622861736372201, 0.07406353866712934]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.5125934493464186, 0.474071986161519, 0.500106245657701, 0.47859706215995956, 0.261816044984851]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.036833616393149526, 0.03251116742308113, 0.03521675425047022, 0.03282282304295947, 0.020855970667678747]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.5085781246017405, 0.4349364487541507, 0.46771554739565957, 0.4353488313244398, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.7499139221833602, 0.6140674398462487, 0.6831950062710597, 0.6145553577458003, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.74201172

comfort:  [1.9169529900752416, 2.04356202042376, 1.9057947393400596, 2.0519259807816113, 0.7259263112016114]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [1.0621127223192914, 1.1392535211135204, 1.0609903565588503, 1.146995389682541, 0.9149421614375086]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [2.0053010701790903, 1.9849061455707897, 1.9913082727961502, 1.9883477385812185, 1.0601540100424884]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [2.00072593319225, 1.99624767073594, 1.9988133210209398, 1.9969875017649485, 1.1120615963049012]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.4104504843209611, 0.0, 0.4471212101846298, 0.2881032585947416]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.005990265045380028, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.7436000193616188, 0.92021896951373, 0.7432161381937199, 0.9219086104189387, 0.2280814704838896]
occs:  [0.0, 0.0, 0.0, 0.0, 0.0]
comfort:  [0.0, 0.0,

comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.0, 0.0, 0.0, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.08046572059625134, 0.0, 0.08841435287612143, 0.0, 0.0]
occs:  [11.0, 5.0, 11.0, 5.0, 20.0]
comfort:  [0.2388862508852192, 0

In [6]:
print(
    'Mean reward: ',
    np.mean(rewards),
    'Cumulative reward: ',
    sum(rewards))

Mean reward:  -1.769617608534603 Cumulative reward:  -62007.40100305364


In [7]:
env.close()

[2023-05-17 09:22:52,341] EPLUS_ENV_demo-v1_MainThread_ROOT INFO:EnergyPlus simulation closed successfully. 


In [7]:
test_str = ["asd"]
test_list = ["asdkj", "askdj"]

if (type(test_str) == type(test_list)):
    print('OKAY')
    if (type(test_str) == list and len(test_str) != len(test_list)):
        print("Lists length don't match")
else: 
    print('not same type')

OKAY
Lists length don't match


In [9]:
for idx, item in enumerate(test_list):
    print(idx, item)

0 asdkj
1 askdj


In [7]:
zone_occ = 0.0
weight = 0.5 if zone_occ > 0.0 else 0.75
print(weight)

0.75
